In [2]:
#Load Libraries
import torch
import torch.nn as nn
import torchvision.datasets as datasets
import torchvision.transforms as transforms
import torch.nn.init
from torch.utils.data import Dataset
from torch.autograd import Variable
from PIL import Image
from torch.utils.data import DataLoader
import matplotlib.pyplot as plt
from tqdm import tqdm
#import helper
import numpy as np


# GPU 설정
device = 'cuda' if torch.cuda.is_available() else 'cpu'

# 랜덤 시드 고정
torch.manual_seed(123)

# GPU 사용 가능일 경우 랜덤 시드 고정
if device == 'cuda':
    torch.cuda.manual_seed_all(123)

# Define a transform to normalize the data
transform = transforms.Compose([transforms.ToTensor(), transforms.Normalize(mean=(0.5,), std=(0.5,))])

In [3]:
from PIL import Image
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
import torchvision


In [4]:
#커스텀 데이터
trans = transforms.Compose([transforms.Resize((28,28)), transforms.ToTensor(),transforms.Normalize(mean=(0.5,), std=(0.5,))])

deer = torchvision.datasets.ImageFolder(root = "E:/LAB/datasets/CustomDatasets", transform=trans)
deer_trainloader = torch.utils.data.DataLoader(deer,batch_size=32,shuffle=True)

notdeer = torchvision.datasets.ImageFolder(root="E:/LAB/datasets/afhq/train", transform=trans)
deer_testloader = torch.utils.data.DataLoader(notdeer,batch_size=32,shuffle=True)

In [128]:
print(len(deer))

1265


In [2]:
# Download and load the training data
fashion_trainset = datasets.FashionMNIST('~/.pytorch/F_MNIST_data/', download=True, train=True, transform=transform)
fashion_trainloader = torch.utils.data.DataLoader(fashion_trainset, batch_size=128, shuffle=True)

# Download and load the test data
fashion_testset = datasets.FashionMNIST('~/.pytorch/F_MNIST_data/', download=True, train=False, transform=transform)
fashion_testloader = torch.utils.data.DataLoader(fashion_testset, batch_size=128, shuffle=True)

In [3]:
# Download and load the training data
mnist_trainset = datasets.MNIST('~/.pytorch/MNIST_data/', download=True, train=True, transform=transform)
mnist_trainloader = torch.utils.data.DataLoader(mnist_trainset, batch_size=128, shuffle=True)

# Download and load the test data
mnist_testset = datasets.MNIST('~/.pytorch/MNIST_data/', download=True, train=False, transform=transform)
mnist_testloader = torch.utils.data.DataLoader(mnist_testset, batch_size=128, shuffle=True)

In [482]:
class CNN(torch.nn.Module):

    def __init__(self):
        super(CNN, self).__init__()
        # 첫번째층
        # ImgIn shape=(?, 28, 28, 1)
        #    Conv     -> (?, 28, 28, 32)
        #    Pool     -> (?, 14, 14, 32)
        self.layer1 = torch.nn.Sequential(
            torch.nn.Conv2d(3, 32, kernel_size=3, stride=1, padding=1),
            torch.nn.ReLU(),
            torch.nn.MaxPool2d(kernel_size=2, stride=2))

        # 두번째층
        # ImgIn shape=(?, 14, 14, 32)
        #    Conv      ->(?, 14, 14, 64)
        #    Pool      ->(?, 7, 7, 64)
        self.layer2 = torch.nn.Sequential(
            torch.nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            torch.nn.ReLU(),
            torch.nn.MaxPool2d(kernel_size=2, stride=2))

        self.last_layer = torch.nn.Sequential(
            torch.nn.Conv2d(64,128, kernel_size=3, stride=1, padding=1),
            torch.nn.ReLU(),
            torch.nn.MaxPool2d(kernel_size=3, stride=2, padding=1),
        )
        self.fc1 = torch.nn.Linear(4*4*128,2,bias=True)
        torch.nn.init.xavier_uniform_(self.fc1.weight)
        self.layer4 = torch.nn.Sequential(
            self.fc1,
            torch.nn.ReLU()
        )
        # 전결합층 한정으로 가중치 초기화
    #    torch.nn.init.xavier_uniform_(self.fc.weight)

    def forward(self, x):
        out = self.layer1(x)
        out = self.layer2(out)
        out = self.last_layer(out)
        out = out.view(out.size(0), -1)   # 전결합층을 위해서 Flatten
        out = self.layer4(out)
        return out

In [497]:
class CNN(torch.nn.Module):

    def __init__(self):
        super(CNN, self).__init__()
        
        self.keep_prob = 0.5
        # L1 ImgIn shape=(?, 28, 28, 1)
        #    Conv     -> (?, 28, 28, 32)
        #    Pool     -> (?, 14, 14, 32)
        self.layer1 = torch.nn.Sequential(
            torch.nn.Conv2d(3, 32, kernel_size=3, stride=1, padding=1),
            torch.nn.ReLU(),
            torch.nn.MaxPool2d(kernel_size=2, stride=2))
        # L2 ImgIn shape=(?, 14, 14, 32)
        #    Conv      ->(?, 14, 14, 64)
        #    Pool      ->(?, 7, 7, 64)
        self.layer2 = torch.nn.Sequential(
            torch.nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            torch.nn.ReLU(),
            torch.nn.MaxPool2d(kernel_size=2, stride=2))
        
        # L3 ImgIn shape=(?, 7, 7, 64)
        #    Conv      ->(?, 7, 7, 32)
        #    Pool      ->(?, 4, 4, 32)
        self.layer3 = torch.nn.Sequential(
            torch.nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            torch.nn.ReLU(),
            torch.nn.MaxPool2d(kernel_size=2,stride=2, padding=1)
        )
        # # L4 FC 4x4x128 inputs -> 625 outputs
        self.fc1 = torch.nn.Linear(4 * 4 * 128, 625, bias=True)
        torch.nn.init.xavier_uniform_(self.fc1.weight)
        self.layer4 = torch.nn.Sequential(
            self.fc1,
            torch.nn.ReLU(),
            torch.nn.Dropout(p=1 - self.keep_prob))

        # L5 Final FC 625 inputs -> 10 outputs
        self.fc2 = torch.nn.Linear(625, 2, bias=True)
        torch.nn.init.xavier_uniform_(self.fc2.weight)

    def forward(self, x):
        out = self.layer1(x)
        out = self.layer2(out)
        out = self.layer3(out)
        out = out.view(out.size(0), -1)
        out = self.layer4(out)
        out = self.fc2(out)
        return out

In [498]:
#Set hyper-parameter
learning_rate = 0.001
#training_epochs = 50
training_epochs = 1
# 해당 논문에서는 만번의 epoch를 수행했지만 computation power로 인해 epoch 50회 수행
batch_size = 32

In [499]:
#deer CNN 모델 정의
deer_model = CNN().to(device)

criterion = torch.nn.CrossEntropyLoss().to(device)
optimizer = torch.optim.Adam(deer_model.parameters(), lr=learning_rate)

total_batch = len(deer_trainloader)
print('총 배치의 수 : {}'.format(total_batch))

총 배치의 수 : 40


In [500]:
# deer_model(CNN)
X_trains = []
X_trains_correct = []


for epoch in range(training_epochs):
    avg_cost = 0
    for X, Y in (deer_trainloader):
        X = X.to(device)
        Y = Y.to(device)
        optimizer.zero_grad()
        hypothesis = deer_model(X)

        if epoch == training_epochs - 1:
            for hypo in range(len(hypothesis)):
                x = []
                for i in hypothesis[hypo]:
                    x.append(i.item())
            #print(y)
                X_trains.append(x)

        cost = criterion(hypothesis, Y)

        cost.backward()
        optimizer.step()
        avg_cost += cost / total_batch

    print('[Epoch: {:>4}] cost = {:>.9}'.format(epoch + 1, avg_cost))


[Epoch:    1] cost = 0.0217818301


In [501]:
# CNN_Train_Predict
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in deer_trainloader:
        X = X.to(device)
        Y = Y.to(device)
        prediction = deer_model(X)
        print(prediction)
        predicted = torch.argmax(prediction,1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

print('Test Accuracy images: {} %'.format(100 * correct / total))

tensor([[ 108.9207, -104.8864],
        [ 111.5342, -112.0401],
        [ 112.1289, -100.3120],
        [ 132.4752, -119.0382],
        [ 108.8585,  -98.4887],
        [  96.7960,  -98.6958],
        [ 112.9453, -115.8619],
        [ 119.0141, -122.9750],
        [ 121.2848, -106.2888],
        [ 117.6765, -104.7877],
        [ 127.5977, -111.7899],
        [  68.9811,  -91.4735],
        [ 102.0343, -124.1796],
        [  94.0274,  -88.9936],
        [ 104.3986, -104.8279],
        [  79.9882,  -83.8923],
        [ 104.9048, -115.6093],
        [  91.1232,  -90.0371],
        [  97.7431, -105.1619],
        [ 129.3329, -107.9782],
        [  96.8143, -103.0082],
        [  81.9429,  -89.5151],
        [  99.1951, -108.7627],
        [ 125.7112, -113.9513],
        [  93.9067,  -87.3868],
        [  61.3792,  -72.1346],
        [  69.2083,  -67.1176],
        [  83.3993,  -97.4570],
        [  74.6142,  -73.1025],
        [ 125.0938, -129.6052],
        [  98.1211, -102.8144],
        

In [502]:
# CNN_Test_Predict
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in deer_testloader:
        X = X.to(device)
        for i in range(len(Y)):
            Y[i] = 1
        Y = Y.to(device)
        prediction = deer_model(X)
        print(prediction)
        predicted = torch.argmax(prediction,1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

print('Test Accuracy of the model on the 10000 test images: {} %'.format(100 * correct / total))

tensor([[ 121.2891, -129.4608],
        [ 130.5776, -146.2636],
        [  73.1066,  -89.3265],
        [ 113.1812,  -94.3059],
        [ 111.2112, -107.1517],
        [ 107.4224, -108.5198],
        [  99.3532,  -98.8010],
        [ 113.9531, -123.6727],
        [ 127.5428, -108.9684],
        [ 121.2648, -122.9760],
        [ 116.3953, -112.0076],
        [ 114.4965, -117.6306],
        [ 128.2234, -109.5141],
        [ 151.3030, -138.2856],
        [  73.4029,  -85.9034],
        [ 141.8067, -135.6854],
        [  90.8788,  -97.9786],
        [ 124.1772, -114.3903],
        [ 110.8297, -119.4184],
        [  82.3587,  -75.4279],
        [ 107.8517, -109.9400],
        [  86.4101, -100.1685],
        [ 113.6411, -114.9474],
        [ 130.3626, -126.7452],
        [  86.7862,  -72.3810],
        [ 112.4795,  -87.2666],
        [  96.5356,  -94.2959],
        [ 123.6088, -124.1658],
        [ 107.7000, -105.1379],
        [ 114.1218, -109.9320],
        [ 103.3719, -108.8371],
        

In [ ]:
print(len(X_tests))

14630


In [ ]:
print('\n'.join(map(str,X_tests[:10])))

[12.489908218383789, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[13.574064254760742, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[11.416069984436035, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.4747679829597473, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.415172815322876, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[17.67763328552246, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0

In [ ]:
print(X_tests)

[[12.489908218383789, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [13.574064254760742, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [11.416069984436035, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.4747679829597473, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.415172815322876, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [17.67763328552246, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,

In [460]:
from sklearn.svm import OneClassSVM
clf = OneClassSVM(gamma='auto',kernel='rbf')
clf.fit(X_trains)

OneClassSVM(gamma='auto')

In [461]:
x_predict = clf.predict(X_trains)

In [462]:
correct = 0
for i in range(1265):
    print(x_predict[i])
    if x_predict[i] == 1: correct+=1
correct = correct*100//1265.0
print("acuracy: {0}%".format(correct))

-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-

In [ ]:
X_test_predict = clf.predict(X_tests)

In [373]:
#test svm
correct = 0
for i in range(len(X_test_predict)):
    if X_test_predict[i] == -1: correct+=1
correct = correct*100//len(X_test_predict)
print("acuracy: {0}%".format(correct))

acuracy: 99%
